In [1]:
import os
os.chdir("../")

# PII Detection: Data EDA

In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from src.data import rebuild_text

## Datasets

### Loading

#### Competition's Data

In [3]:
comp_df = pd.read_json("Dataset/competition/train.json")
comp_df.head(2)

document                                          full_text  \
0         7  Design Thinking for innovation reflexion-Avril...   
1        10  Diego Estrada\n\nDesign Thinking Assignment\n\...   

                                              tokens  \
0  [Design, Thinking, for, innovation, reflexion,...   
1  [Diego, Estrada, \n\n, Design, Thinking, Assig...   

                                 trailing_whitespace  \
0  [True, True, True, True, False, False, True, F...   
1  [True, False, False, True, True, False, False,...   

                                              labels  
0  [O, O, O, O, O, O, O, O, O, B-NAME_STUDENT, I-...  
1  [B-NAME_STUDENT, I-NAME_STUDENT, O, O, O, O, O...

In [4]:
comp_df.shape

(6807, 5)

#### [Nicholas Broad](https://www.kaggle.com/datasets/nbroad/pii-dd-mistral-generated) (Mistral 7B)

In [5]:
nbroad_df = pd.read_json("Dataset/nbroad/mixtral-8x7b-v1.json")
nbroad_df.head(2)

document                                          full_text  \
0  dtduupvzgt  Tiburce Evans, https://www.instagram.com/tibur...   
1  uejmzisyyh  Rose-Mai Rodriguez | PIN # 3814374\n501 Andrea...   

                                              tokens  \
0  [Tiburce, Evans, ,, https://www.instagram.com/...   
1  [Rose, -, Mai, Rodriguez, |, PIN, #, 3814374, ...   

                                              labels  \
0  [B-NAME_STUDENT, I-NAME_STUDENT, O, B-URL_PERS...   
1  [B-NAME_STUDENT, I-NAME_STUDENT, I-NAME_STUDEN...   

                                 trailing_whitespace  
0  [True, False, True, False, True, True, True, F...  
1  [False, False, True, True, True, True, True, F...

In [6]:
nbroad_df.shape

(2355, 5)

#### [Pj Mathematician](https://www.kaggle.com/competitions/pii-detection-removal-from-educational-data/discussion/470921) (GPT 3.5)

In [7]:
pjm_df = pd.read_json("Dataset/pjm_moth/pii_dataset_fixed.json")
pjm_df.head(2)

document  \
0  001010b6-de5c-4a96-bd1f-c8b2b0f15ccc   
1  0016aef8-0d26-45fe-bb7d-ef05311d6383   

                                           full_text  \
0  In my role as a dietician, I have encountered ...   
1  Hello, my name is Oleg Ivanova, and I'm a geol...   

                                              tokens  \
0  [In, my, role, as, a, dietician, ,, I, have, e...   
1  [Hello, ,, my, name, is, Oleg, Ivanova, ,, and...   

                                 trailing_whitespace  \
0  [True, True, True, True, True, False, True, Tr...   
1  [False, True, True, True, True, True, False, T...   

                                              labels  
0  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
1  [O, O, O, O, O, B-NAME_STUDENT, I-NAME_STUDENT...

In [8]:
pjm_df.shape

(4434, 5)

#### [No Fit Just Luck](kaggle.com/datasets/tonyarobertson/mixtral-original-prompt) (Mistral 7B)

In [9]:
nfjl_df = pd.read_json("Dataset/no_fit_just_luck/Fake_data_1850_218.json")
nfjl_df.head(2)

document                                          full_text  \
0         0  Leveraging Lean Methodology to Optimize Hospit...   
1         1  From Chaos to Calm: Addressing Complex Challen...   

                                              tokens  \
0  [Leveraging, Lean, Methodology, to, Optimize, ...   
1  [From, Chaos, to, Calm, :, Addressing, Complex...   

                                 trailing_whitespace  \
0  [True, True, True, True, True, True, False, Tr...   
1  [True, True, True, False, True, True, True, Tr...   

                                              labels  
0  [O, O, O, O, O, O, O, O, O, O, O, O, B-NAME_ST...  
1  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...

In [10]:
nfjl_df.shape

(1850, 5)

#### [Mpware](https://www.kaggle.com/datasets/mpware/pii-mixtral8x7b-generated-essays) (Mixtral8x7B)

In [11]:
mpware_df = pd.read_json("Dataset/mpware/mpware_mixtral8x7b_v1.1-no-i-username.json")
mpware_df.head(2)

document  \
0  2cd5fb9799fe06349528c33423a0f595   
1  3cb7ffeb0ef2f45672e53c38b29d610c   

                                           full_text  \
0  Storytelling Challenge: Crafting Compelling Na...   
1  Storytelling Challenge: The Power of Narrative...   

                                              tokens  \
0  [Storytelling, Challenge, :, Crafting, Compell...   
1  [Storytelling, Challenge, :, The, Power, of, N...   

                                 trailing_whitespace  \
0  [True, False, True, True, True, True, True, Tr...   
1  [True, False, True, True, True, True, True, Tr...   

                                              labels  
0  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
1  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...

In [12]:
mpware_df.shape

(2692, 5)

#### [Dileep](https://www.kaggle.com/datasets/dileepjayamal/pii-detect-gpt3-5-synthetic-data-8k) (GPT 3.5)

In [13]:
dileep_df = pd.read_json("Dataset/dileep/PII_Detect_GPT3.5_Generated_data_v1.json")
dileep_df["full_text"] = dileep_df.apply(lambda row: rebuild_text(row["tokens"], row["trailing_whitespace"]), axis=1)
dileep_df["document"] = list(range(dileep_df.shape[0]))
dileep_df.head(2)

tokens  \
0  [Design, Thinking, for, innovation, reflexion,...   
1  [Rachel, Hughes, \n\n, Design, Thinking, Assig...   

                                 trailing_whitespace  \
0  [True, True, True, True, False, False, True, F...   
1  [True, False, False, True, True, False, False,...   

                                              labels  \
0  [O, O, O, O, O, O, O, O, O, B-NAME_STUDENT, I-...   
1  [B-NAME_STUDENT, I-NAME_STUDENT, O, O, O, O, O...   

                                           full_text  document  
0  Design Thinking for innovation reflexion-May 2...         0  
1  Rachel Hughes\n\nDesign Thinking Assignment\n\...         1

In [14]:
dileep_df.shape

(8281, 5)

#### [Valentin Warner's Label Specific Dataset](https://www.kaggle.com/datasets/valentinwerner/pii-label-specific-data) (Mistral 7B)

In [15]:
valentin_df = pd.read_json("Dataset/valentin/all_labels.json")
valentin_df["full_text"] = valentin_df.apply(lambda row: rebuild_text(row["tokens"], row["trailing_whitespace"]), axis=1)
valentin_df["document"] = list(range(valentin_df.shape[0]))
valentin_df.head(2)

tokens  \
0  [ , Title, :, Home, at, 958, Ryan, Ports, ,, J...   
1  [ , Title, :, My, Home, at, 7600, David, Plain...   

                                 trailing_whitespace  \
0  [False, False, True, True, True, True, True, F...   
1  [False, False, True, True, True, True, True, T...   

                                              labels  \
0  [O, O, O, O, O, B-STREET_ADDRESS, I-STREET_ADD...   
1  [O, O, O, O, O, O, B-STREET_ADDRESS, I-STREET_...   

                                           full_text  document  
0   Title: Home at 958 Ryan Ports, Jamesstad, FL ...         0  
1   Title: My Home at 7600 David Plains, Port Hea...         1

In [16]:
valentin_df.shape

(4367, 5)

#### [Moth](https://www.kaggle.com/datasets/alejopaullier/pii-external-dataset/data) (Gemini)

In [17]:
moth_df = pd.read_json("Dataset/pjm_moth/moredata_dataset_fixed.json")
moth_df.head(2)

document                                          full_text  \
0     pj_0  In today's modern world, where technology has ...   
1     pj_1  In today's modern world, where technology has ...   

                                              tokens  \
0  [In, today, 's, modern, world, ,, where, techn...   
1  [In, today, 's, modern, world, ,, where, techn...   

                                 trailing_whitespace  \
0  [True, False, True, True, False, True, True, T...   
1  [True, False, True, True, False, True, True, T...   

                                              labels  
0  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
1  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...

In [18]:
moth_df.shape

(2000, 5)

#### [Newton](https://www.kaggle.com/datasets/newtonbaba12345/pii-detection-gemini-created-dataset) (Gemini)

In [19]:
newton_df = pd.concat([
    pd.read_json("Dataset/newton/pii_dataset_Gemini_NEWTON_BABA.json"),
    pd.read_json("Dataset/newton/pii_dataset_gemma.json"),
])
newton_df.head(2)

document                                          full_text  \
0  1111555001  As an essay writer, I am tasked with the respo...   
1  1111555002  Tyler Lopez, a diligent student with the usern...   

                                              tokens  \
0  [As, an, essay, writer, ,, I, am, tasked, with...   
1  [Tyler, Lopez, ,, a, diligent, student, with, ...   

                                 trailing_whitespace  \
0  [True, True, True, False, True, True, True, Tr...   
1  [True, False, True, True, True, True, True, Tr...   

                                              labels  
0  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
1  [O, O, B-PHONE_NUM, O, O, O, O, O, O, O, O, I-...

In [20]:
newton_df.shape

(5169, 5)

### Adding Source and Generation Info

In [21]:
def add_source_and_generation_info(df: pd.DataFrame, source: str, generation: str) -> pd.DataFrame:
    df["source"] = source
    df["generation"] = generation
    return df

In [22]:
comp_df = add_source_and_generation_info(comp_df, "competition", "competition")
nbroad_df = add_source_and_generation_info(nbroad_df, "nbraod", "mistral_7B")
pjm_df = add_source_and_generation_info(pjm_df, "pjmathematician", "gpt3.5")
nfjl_df = add_source_and_generation_info(nfjl_df, "no_fit_just_luck", "mistral_7B")
mpware_df = add_source_and_generation_info(mpware_df, "mpware", "mistral_7B")
dileep_df = add_source_and_generation_info(dileep_df, "dileep", "gpt3.5")
valentin_df = add_source_and_generation_info(valentin_df, "valentin", "mistral_7B")
moth_df = add_source_and_generation_info(moth_df, "moth", "Gemini")
newton_df = add_source_and_generation_info(newton_df, "newton", "Gemini")

### Combining Together

In [23]:
df = pd.concat(
    [
        comp_df,
        nbroad_df,
        pjm_df,
        nfjl_df,
        mpware_df,
        dileep_df,
        valentin_df,
        moth_df,
        newton_df,
    ]
)
df["document"] = list(range(df.shape[0]))
df.set_index("document", inplace=True)
del comp_df, nbroad_df, pjm_df, nfjl_df, mpware_df, dileep_df, valentin_df, moth_df, newton_df

In [24]:
df.shape

(37955, 6)

In [25]:
df.columns

Index(['full_text', 'tokens', 'trailing_whitespace', 'labels', 'source',
       'generation'],
      dtype='object')

## Label Distribution

In [26]:
from sklearn.preprocessing import MultiLabelBinarizer

In [27]:
def encode_labels(df):
    df["unique_labels"] = df["labels"].apply(
        lambda x: list(set([l.split("-")[1] for l in x if l != "O"]))
    )

    # add 1-hot encoding
    mlb = MultiLabelBinarizer()
    one_hot_encoded = mlb.fit_transform(df["unique_labels"])
    one_hot_df = pd.DataFrame(one_hot_encoded, columns=mlb.classes_)
    df = pd.concat([df, one_hot_df], axis=1)

    # add 'OTHER' column
    df["NO_PII"] = df["unique_labels"].apply(lambda x: 1 if len(x) == 0 else 0)

    return df, list(mlb.classes_) + ["NO_PII"]

In [28]:
df, label_classes = encode_labels(df)

for col in label_classes:
    print(f'{col}: {df[col].sum()}')

EMAIL: 9303
ID_NUM: 5581
NAME_STUDENT: 17809
PHONE_NUM: 9568
STREET_ADDRESS: 12101
URL_PERSONAL: 6472
USERNAME: 6611
NO_PII: 13810


#### Globally

In [29]:
columns = [
    "EMAIL",
    "ID_NUM",
    "NAME_STUDENT",
    "PHONE_NUM",
    "STREET_ADDRESS",
    "URL_PERSONAL",
    "USERNAME",
    "NO_PII",
]
fig = px.bar(df[columns].sum(), text_auto=True)
fig.update_layout(
    height=400,
    width=1200,
    title_x=0.5,
    title_text=f"Label Count<br><sup>Globally</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", y=-0.2, x=0.5),
)
fig.show()

#### By Source

In [30]:
grouped_df = df.groupby("source")[columns].sum()
fig = px.bar(grouped_df, barmode="group", text_auto=True)
fig.update_layout(
    height=400,
    width=1200,
    title_x=0.5,
    title_text=f"Label Count<br><sup>By Dataset Source</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", y=-0.2, x=0.5),
)
fig.show()

In [31]:
fig = px.imshow(grouped_df, text_auto=True)
fig.update_layout(
    height=600,
    width=600,
    title_x=0.5,
    title_text=f"Label Count Heatmap<br><sup>By Dataset Source</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", y=-0.2, x=0.5),
)
fig.show()

#### By LLM

In [32]:
grouped_df = df.groupby("generation")[columns].sum()
fig = px.bar(grouped_df, barmode="group", text_auto=True)
fig.update_layout(
    height=400,
    width=1200,
    title_x=0.5,
    title_text=f"Label Count<br><sup>By LLM</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", y=-0.2, x=0.5),
)
fig.show()

In [33]:
fig = px.imshow(grouped_df, text_auto=True)
fig.update_layout(
    height=400,
    width=600,
    title_x=0.5,
    title_text=f"Label Count Heatmap<br><sup>By LLM</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", y=-0.2, x=0.5),
)
fig.show()

## Token Length Distribution

In [34]:
df["token_length"] = df.tokens.apply(len)

In [35]:
fig = px.histogram(
    df,
    x="token_length",
    color="NO_PII",
    text_auto=True,
    marginal="box",
    nbins=100,
)
fig.update_layout(
    height=600,
    width=1500,
    title_x=0.5,
    title_text=f"Token Length Distribution<br><sup>Globally</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", y=-0.2, x=0.5),
)
newnames = {"0": "Has PII", "1": "No PII"}
fig.for_each_trace(
    lambda t: t.update(
        name=newnames[t.name],
        legendgroup=newnames[t.name],
        hovertemplate=t.hovertemplate.replace(t.name, newnames[t.name]),
    )
)
fig.show()

In [36]:
fig = px.histogram(df, x="token_length", color="source", nbins=100, marginal="box", text_auto=True)
fig.update_layout(
    height=1000,
    width=1500,
    title_x=0.5,
    title_text=f"Token Length Distribution<br><sup>By Source</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", x=0.5),
)
fig.show()

In [37]:
fig = px.histogram(df, x="token_length", color="generation", nbins=100, marginal="box", text_auto=True)
fig.update_layout(
    height=1000,
    width=1500,
    title_x=0.5,
    title_text=f"Token Length Distribution<br><sup>By LLM</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", x=0.5),
)
fig.show()

## Token Placement Distribution

In [38]:
from itertools import chain

In [39]:
all_labels = sorted(list(set(chain(*[x for x in df.labels.values]))))
all_labels

['B-EMAIL',
 'B-ID_NUM',
 'B-NAME_STUDENT',
 'B-PHONE_NUM',
 'B-STREET_ADDRESS',
 'B-URL_PERSONAL',
 'B-USERNAME',
 'I-EMAIL',
 'I-ID_NUM',
 'I-NAME_STUDENT',
 'I-PHONE_NUM',
 'I-STREET_ADDRESS',
 'I-URL_PERSONAL',
 'I-USERNAME',
 'O']

In [40]:
tracker = {key: [0] * df.token_length.max() for key in all_labels}

for _, row in df.iterrows():
    labels = row.labels

    for idx, label in enumerate(labels):
        tracker[label][idx] += 1

In [41]:
tracker = pd.DataFrame(tracker)
tracker.head()

B-EMAIL  B-ID_NUM  B-NAME_STUDENT  B-PHONE_NUM  B-STREET_ADDRESS  \
0        2         8            5170            7                54   
1        2         0             349           10                 1   
2        0         0             441           39                11   
3      363         6            1094          349               393   
4        1        68             565           68                13   

   B-URL_PERSONAL  B-USERNAME  I-EMAIL  I-ID_NUM  I-NAME_STUDENT  I-PHONE_NUM  \
0              83           0        0         0               0            0   
1               1           4        0         0            5046            1   
2              13           0        0         0             704            1   
3             433         373        0         0             787            2   
4               4           5        0         2            1103          243   

   I-STREET_ADDRESS  I-URL_PERSONAL  I-USERNAME      O  
0                 0               0           0  32631  
1                 5               0           0  32536  
2                 2               0           0  36744  
3                10               0           0  34145  
4               396               0           0  35487

In [42]:
fig = make_subplots(len(all_labels) // 3 + 1, 3, subplot_titles=all_labels)

for i, label in enumerate(all_labels):
    row = i // 3 + 1
    col = (i % 3) + 1
    fig.add_trace(
        go.Histogram(x=tracker[label], nbinsx=32, name=label, texttemplate="%{y}"),
        row=row,
        col=col,
    )

fig.update_layout(
    height=1000,
    width=1500,
    title_x=0.5,
    title_text=f"Label Distribution<br><sup>By Index Position</sup>",
)
fig.update_traces(showlegend=False)
fig.show()

## Number of Labels Appearing Together

In [44]:
df["unique_label_count"] = df.unique_labels.apply(len)

In [45]:
fig = make_subplots(2, 1, shared_xaxes=True)

fig.add_trace(
    go.Histogram(
        x=df[df.source == "competition"].unique_label_count,
        name="Competition Training Data",
        texttemplate="%{y}"
    ),
    row=1,
    col=1,
)
fig.add_trace(
    go.Histogram(
        x=df[df.source != "competition"].unique_label_count,
        name="Synthetic Training Data",
        texttemplate="%{y}"
    ),
    row=2,
    col=1,
)
fig.update_layout(
    height=600,
    width=1500,
    title_x=0.5,
    title_text=f"Label Count<br><sup>Number of Unique Labels per Example</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", x=0.5),
)
fig.show()

In [53]:
def get_pii_tokens(row):
    labels, tokens = row.labels, row.tokens
    return [
        t
        for l, t in zip(labels, tokens)
        if l != "O"
    ]

In [56]:
df["pii_tokens"] = df.apply(get_pii_tokens, axis=1)
df["pii_token_count"] = df.pii_tokens.apply(len)

In [60]:
fig = make_subplots(2, 1, shared_xaxes=True)

fig.add_trace(
    go.Histogram(
        x=df[df.source == "competition"].pii_token_count,
        nbinsx=16,
        name="Competition Training Data",
        texttemplate="%{y}"
    ),
    row=1,
    col=1,
)
fig.add_trace(
    go.Histogram(
        x=df[df.source != "competition"].pii_token_count,
        nbinsx=16,
        name="Synthetic Training Data",
        texttemplate="%{y}"
    ),
    row=2,
    col=1,
)
fig.update_layout(
    height=600,
    width=1500,
    title_x=0.5,
    title_text=f"Label Count<br><sup>Number of PII tokens per Example</sup>",
    legend=dict(orientation="h", yanchor="top", xanchor="center", x=0.5),
)
fig.show()

## Textual Variance